## REMBERT PIPELINE

In [2]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 4.6 MB/s 
     |████████████████████████████████| 5.5 MB 62.8 MB/s 
     |████████████████████████████████| 1.3 MB 69.8 MB/s 
     |████████████████████████████████| 7.6 MB 72.2 MB/s 
     |████████████████████████████████| 441 kB 86.0 MB/s 
     |████████████████████████████████| 9.2 MB 78.1 MB/s 
     |████████████████████████████████| 43 kB 2.3 MB/s 
     |████████████████████████████████| 1.9 MB 67.7 MB/s 
     |████████████████████████████████| 163 kB 82.2 MB/s 
     |████████████████████████████████| 166 kB 85.3 MB/s 
     |████████████████████████████████| 182 kB 84.6 MB/s 
     |████████████████████████████████| 63 kB 2.0 MB/s 
     |████████████████████████████████| 166 kB 86.8 MB/s 
     |████████████████████████████████| 162 kB 91.0 MB/s 
     |████████████████████████████████| 162 kB 85.0 MB/s 
     |██████████████████████████████

In [3]:
# Load the dataset from google drive
from google.colab import drive
drive.mount('/content/drive')

# Import downsampled dataset
df = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_downsampled.xlsx')

# Import without google drive
# df = pd.read_excel('DATASET_downsampled.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Mounted at /content/drive
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [4]:
# Show the distribution of the labels
print(df['labels'].value_counts())

0    648
2    648
3    648
1    648
Name: labels, dtype: int64


In [5]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [6]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'rembert',
    'google/rembert',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Downloading:   0%|          | 0.00/686 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/2.30G [00:00<?, ?B/s]

Some weights of RemBertForSequenceClassification were not initialized from the model checkpoint at google/rembert and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Downloading:   0%|          | 0.00/263 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.70M [00:00<?, ?B/s]

...

{'mcc': 0.8969375507892126, 'f1': array([0.93793103, 0.92307692, 0.95833333, 0.864     ]), 'acc': 0.9227799227799228, 'recall': array([0.97142857, 0.92307692, 0.95833333, 0.83076923]), 'precision': array([0.90666667, 0.92307692, 0.95833333, 0.9       ]), 'eval_loss': 0.2882636580616236}
results accuracy [0.7538461538461538, 0.7807692307692308, 0.7799227799227799, 0.7876447876447876, 0.8455598455598455, 0.8532818532818532, 0.8803088803088803, 0.8841698841698842, 0.9227799227799228]
Mean-Precision: 0.832031482031482
results f1:  [array([0.8951049 , 0.66141732, 0.816     , 0.624     ]), array([0.87878788, 0.73972603, 0.88235294, 0.58490566]), array([0.88      , 0.75555556, 0.83333333, 0.65079365]), array([0.92561983, 0.70503597, 0.88      , 0.66165414]), array([0.91729323, 0.83333333, 0.88073394, 0.75      ]), array([0.93129771, 0.84210526, 0.85483871, 0.77477477]), array([0.95104895, 0.88405797, 0.90598291, 0.76666667]), array([0.94573643, 0.87804878, 0.87769784, 0.83464567]), array([0.9

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.8766989175148575, 'f1': array([0.94285714, 0.90510949, 0.9122807 , 0.86614173]), 'acc': 0.9073359073359073, 'recall': array([0.97058824, 0.92537313, 0.89655172, 0.83333333]), 'precision': array([0.91666667, 0.88571429, 0.92857143, 0.90163934]), 'eval_loss': 0.47114046414693195}
results accuracy [0.7538461538461538, 0.7807692307692308, 0.7799227799227799, 0.7876447876447876, 0.8455598455598455, 0.8532818532818532, 0.8803088803088803, 0.8841698841698842, 0.9227799227799228, 0.9073359073359073]
Mean-Precision: 0.8395619245619246
results f1:  [array([0.8951049 , 0.66141732, 0.816     , 0.624     ]), array([0.87878788, 0.73972603, 0.88235294, 0.58490566]), array([0.88      , 0.75555556, 0.83333333, 0.65079365]), array([0.92561983, 0.70503597, 0.88      , 0.66165414]), array([0.91729323, 0.83333333, 0.88073394, 0.75      ]), array([0.93129771, 0.84210526, 0.85483871, 0.77477477]), array([0.95104895, 0.88405797, 0.90598291, 0.76666667]), array([0.94573643, 0.87804878, 0.87769784, 0.

In [7]:
print("results accuracy",resultsAcc)
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.7538461538461538, 0.7807692307692308, 0.7799227799227799, 0.7876447876447876, 0.8455598455598455, 0.8532818532818532, 0.8803088803088803, 0.8841698841698842, 0.9227799227799228, 0.9073359073359073]
results f1:  [array([0.8951049 , 0.66141732, 0.816     , 0.624     ]), array([0.87878788, 0.73972603, 0.88235294, 0.58490566]), array([0.88      , 0.75555556, 0.83333333, 0.65079365]), array([0.92561983, 0.70503597, 0.88      , 0.66165414]), array([0.91729323, 0.83333333, 0.88073394, 0.75      ]), array([0.93129771, 0.84210526, 0.85483871, 0.77477477]), array([0.95104895, 0.88405797, 0.90598291, 0.76666667]), array([0.94573643, 0.87804878, 0.87769784, 0.83464567]), array([0.93793103, 0.92307692, 0.95833333, 0.864     ]), array([0.94285714, 0.90510949, 0.9122807 , 0.86614173])]
results precision:  [array([0.84210526, 0.7       , 0.80952381, 0.63934426]), array([0.82857143, 0.66666667, 0.9375    , 0.68888889]), array([0.84615385, 0.72857143, 0.80882353, 0.73214286]), array(

In [8]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.890751  0.781010  0.903167  0.787383
Average recall     0.953528  0.850604  0.860263  0.695919
Average F1-Score   0.920568  0.812747  0.880155  0.737758

## Training on the dataset at hand, testing on the 'Trainingskorpus' dataset

In [9]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_Final.xlsx')

# Import without google drive
# testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [10]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [11]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/Trainingskorpus_InitialLabels.xlsx')

# Import without google drive
# testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [12]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [13]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise

equal = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset2['label 1'], testset2['label 2']):
  if(label1 == label2):
    equal[i] = True
  else:
    equal[i] = False
  i += 1
  
testset['equal'] = equal

In [14]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [15]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   74.72 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 74.98 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   73.22 %,  n =  239


In [16]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.885024154589372
Precision D:  0.3968253968253968
Precision I:  0.0
Precision P:  0.5552763819095478
Recall B:  0.8312159709618875
Recall D:  0.7894736842105263
Recall I:  0.0
Recall P:  0.5594936708860759
F1-score B:  0.8572765559195132
F1-score D:  0.528169014084507
F1-score I:  0.0
F1-score P:  0.5573770491803279


/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [17]:
# Calculates the phi-coefficient for labels where both researchers agreed vs. where they disagreed

print('MCC for labels where both researchers agreed: ',matthews_corrcoef(true_label_equal, predicted_labels_equal_initial_label))
print('MCC for labels where both researchers disagreed: ',matthews_corrcoef(true_label_diff, predicted_labels_diff_initial_label))

MCC for labels where both researchers agreed:  0.4997047037033837
MCC for labels where both researchers disagreed:  0.4860296847547065


## Combine dataset at hand and 'Trainingskorpus' dataset, then do Train-Test-Split

In [18]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('/content/drive/MyDrive/KANO Modell Studie/Datasets/LabeledDatasets/DATASET_Trainingskorpus_combined.xlsx')
df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Import without google drive
# df_combined = pd.read_excel('DATASET_Trainingskorpus_combined.xlsx')

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [19]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

2    743
3    743
1    743
0    743
Name: labels, dtype: int64


In [20]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'rembert',
    'google/rembert',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-Precision: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of RemBertForSequenceClassification were not initialized from the model checkpoint at google/rembert and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


...

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.0, 'f1': array([0.        , 0.        , 0.36813187, 0.        ]), 'acc': 0.2255892255892256, 'recall': array([0., 0., 1., 0.]), 'precision': array([0.        , 0.        , 0.22558923, 0.        ]), 'eval_loss': 1.3886076274671053}
results accuracy [0.23154362416107382, 0.2751677852348993, 0.26262626262626265, 0.24915824915824916, 0.27946127946127947, 0.26262626262626265, 0.2222222222222222, 0.265993265993266, 0.26262626262626265, 0.2255892255892256]
Mean-Precision: 0.25370144396990035
results f1:  [array([0.       , 0.       , 0.3760218, 0.       ]), array([0.        , 0.43157895, 0.        , 0.        ]), array([0.   , 0.416, 0.   , 0.   ]), array([0.        , 0.        , 0.        , 0.39892183]), array([0.        , 0.        , 0.        , 0.43684211]), array([0.   , 0.   , 0.416, 0.   ]), array([0.        , 0.        , 0.36363636, 0.        ]), array([0.        , 0.        , 0.42021277, 0.        ]), array([0.   , 0.416, 0.   , 0.   ]), array([0.        , 0.        , 0.3681

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1318: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [21]:
print("results accuracy",resultsAcc2)
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.23154362416107382, 0.2751677852348993, 0.26262626262626265, 0.24915824915824916, 0.27946127946127947, 0.26262626262626265, 0.2222222222222222, 0.265993265993266, 0.26262626262626265, 0.2255892255892256]
results f1:  [array([0.       , 0.       , 0.3760218, 0.       ]), array([0.        , 0.43157895, 0.        , 0.        ]), array([0.   , 0.416, 0.   , 0.   ]), array([0.        , 0.        , 0.        , 0.39892183]), array([0.        , 0.        , 0.        , 0.43684211]), array([0.   , 0.   , 0.416, 0.   ]), array([0.        , 0.        , 0.36363636, 0.        ]), array([0.        , 0.        , 0.42021277, 0.        ]), array([0.   , 0.416, 0.   , 0.   ]), array([0.        , 0.        , 0.36813187, 0.        ])]
results precision:  [array([0.        , 0.        , 0.23154362, 0.        ]), array([0.        , 0.27609428, 0.        , 0.        ]), array([0.        , 0.26262626, 0.        , 0.        ]), array([0.        , 0.        , 0.        , 0.24915825]), array([0

In [22]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.0  0.080135  0.120797  0.052862
Average recall     0.0  0.298795  0.500000  0.200000
Average F1-Score   0.0  0.126358  0.194400  0.083576